In [3]:
#Import Packages 
import xarray as xr
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt 
import os 
import metpy 
import metpy.calc as mpcalc
from metpy.plots import SkewT
from metpy.units import units 
from IPython.display import HTML, display 
import imageio
from tqdm import tqdm
from itertools import product
import wrf 
import glob 
from scipy.interpolate import RegularGridInterpolator, interp1d
from mpl_toolkits.mplot3d import Axes3D
import seaborn as sns
from pathlib import Path
import matplotlib.patches as mpatches
import matplotlib.lines as mlines

In [4]:
# Create Data Paths
#Create Path For Data Collection and Create A List of File Names
storm16_data_path = '/storage/work/bsh5393/storm16/'
storm16_files = os.listdir(storm16_data_path)

#Remove Unneccessary Files From Storm 16 File List
storm16_files.remove('README-TIMELEVELS')
storm16_files.remove('namelist.input')
storm16_files.remove('runstorm16.pbs.o44255112')
storm16_files.remove('cm1out_stats.nc')

# Establish Model Path
model_path = '/storage/group/pmm116/default/bsh5393/cm1sims/'

# Simulation Paths
sim_paths = sorted(glob.glob(model_path + '*SIM*'))
# Sorting function
sim_paths = sorted(sim_paths, key=lambda x: int(x.split('SIM')[1].split('_')[0]))

# Simulation Names
sim_names = sorted(os.listdir(sim_paths[0]))
sim_names = [name for name in sim_names if 'cm1out_00' in name]

# Actual Names of Each Run
run_names = sorted(os.listdir(model_path))
#run_names.remove('cm1test')
#run_names.remove('cm1test2')
#run_names.remove('test_101158')
run_names = sorted(run_names, key=lambda x: int(x.split('SIM')[1].split('_')[0]))

In [5]:
#Step 1: Initialization and Input Parameters

#Data at t = 2hrs
storm_data = xr.open_dataset(storm16_data_path + storm16_files[-1])

#Dataset Domain Size
ni = storm_data['ni']
nj = storm_data['nj']
nk = storm_data['nk']

#Datapoint Locations
x_data = storm_data['xh']*units.kilometer
y_data = storm_data['yh']*units.kilometer
z_data = storm_data['z']*units.kilometer

#Grid Locations (n+1)
x_grid = storm_data['xf']*units.kilometer
y_grid = storm_data['yf']*units.kilometer
z_grid = storm_data['zf']*units.kilometer

#Create New Lower/Upper Bound Variables Since We are not in the center of the domain anymore
lower_bound_x = np.abs(x_data.values + 12.5).argmin()-2
upper_bound_x = np.abs(x_data.values - 12.5).argmin()
lower_bound_y = np.abs(y_data.values + 12.5).argmin()
upper_bound_y = np.abs(y_data.values - 12.5).argmin()+2
horiz_length = upper_bound_y-lower_bound_y

#Grid Size 
size_x = size_y = upper_bound_x-lower_bound_x
size_z = len(z_data)

#Grid Spacing 
dx = x_data[1].values - x_data[0].values
dy = y_data[1].values - y_data[0].values
dz = np.zeros(len(z_data))
dz[0] = z_data[0].values
dz[1:] = z_data[1:].values-z_data[0:-1].values

#Time Intervals of Data
time = []
for x in np.arange(1,len(storm16_files),1):
    t = xr.open_dataset(storm16_data_path + storm16_files[x])['time']
    time.append(t)    
time = (np.asarray(time)*10**-9).reshape(len(time))
time = time.astype('int')
time = time - time[0]+30 #time elapsed in seconds (useful for interpolation later on)

#Time Intervals of Interpolation (We want every 10 seconds)
int_time = np.arange(int(time[0]), int(time[-1]), 10)
nanal = len(int_time) #Number of Trajectory Points 
dt = int_time[1]-int_time[0]

#Input Parameters 
asc_rate = 5 #3 m/s ascent rate of balloon


In [6]:
# Create Global Variables
sample_sim = xr.open_dataset(sim_paths[0]+ '/' + sim_names[0])

# Grid Points
x_grid = sample_sim['xf']
y_grid = sample_sim['yf']
z_grid = sample_sim['zf']

# Scalar Points
x_data = sample_sim['xh']
y_data = sample_sim['yh']
z_data = sample_sim['zh']

# Time Array
time = np.linspace(0, 120, 25, dtype='int')

# Following Code Creates full ensemble dbz snapshots

In [11]:
# Tweak this perhaps to make the facecolor of each textbox represent NT, WT, or ST
# Create A Function that Animates the entire ensemble
# Iterate over each simulation time

# Specify a time for the entire snapshot
t = 12 # 1 hr mark of simulation

# Counter for each simulation
count = 0

# Initialize Figure
fig, axs = plt.subplots(ncols = 6, nrows = 5, figsize = (30, 24), constrained_layout=True, dpi = 400)
fig.subplots_adjust(bottom=0.10, right=0.90)  # Make space below and on the right

# Read in Each Simulation's Data
x_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['xh'] # scalar x-grid
y_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['yh'] # scalar y-grid 
time = np.int(xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes

# Iterate over Each Simulation to Populate the Columns/Rows or Each Panel
for row in tqdm(range(5)):
    for col in range(6):

        # Read in vertical vorticity and reflectivity
        data =  xr.open_dataset(sim_paths[count] + '/' + sim_names[t])[['dbz', 'winterp','zvort']].isel(time=0, zh = [0,17])
        #vorticity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['zvort'].isel(time=0, zh=0) # vertical vorticity at z = 7.5m
        #reflectivity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['dbz'].isel(time = 0, zh = 17) # Relfectivity at z = 522 m
        #velocity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['winterp'].isel(time = 0, zh = 17) # vertical velocity at z= 522 m

        # plotting data 
        vort = axs[row, col].contourf(x_data, y_data, data['zvort'].isel(zh=0), cmap = 'bwr', alpha = 1, levels = np.arange(-.4, .41, .1),
                           vmin = -.4, vmax = .4)
        refl = axs[row, col].contourf(x_data, y_data, data['dbz'].isel(zh=1), levels = np.arange(10,71, 5), vmin = 10, vmax = 70,
                           cmap = 'gist_ncar')
        w = axs[row, col].contour(x_data, y_data, data['winterp'].isel(zh=1), levels = np.arange(5, 31, 5), colors ='k')

        # Manually Set Axis Limits
        axs[row, col].set_xlim(-30, 20)
        axs[row, col].set_ylim(-20, 30)

        # plot titles
        axs[row, col].text(15, 26, f'{count+1}', fontsize=12, 
           bbox=dict(facecolor='palegoldenrod', boxstyle='round,pad=0.2'))
        #axs[row, col].xlabel = 'km'
        #axs[row, col].ylabel = 'km'

        # Update Counter
        count += 1

# Titles for Entire Plot
#plt.suptitle(f'Full Ensemble: t = {5*t} min.', fontsize = 25, y = 0.91)

# --------------------------------------------------------------------------------------------------------------
# Horizontal Colorbar (Bottom)
cbar_ax_h = fig.add_axes([0.17, 0.05, 0.7, 0.025])  # [left, bottom, width, height]
hcolorbar = fig.colorbar(vort, cax=cbar_ax_h, orientation='horizontal')
hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=24)
hcolorbar.ax.tick_params(labelsize=20)  # One-liner to set font size

# Vertical Colorbar (Right)
cbar_ax_v = fig.add_axes([0.91, 0.14, 0.02, 0.7])  # [left, bottom, width, height]
vcolorbar = fig.colorbar(refl, cax=cbar_ax_v, orientation='vertical')
vcolorbar.set_label('dBZ', fontsize=24)
vcolorbar.ax.tick_params(labelsize=20)  # One-liner to set font size


#         # Add global colorbar
#         hcolorbar = fig.colorbar(vort, label = r'$\zeta_{7.5 \, m}$', orientation = 'horizontal', pad = 0.075, shrink=0.9)
#         hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=14)
#         vcolorbar = fig.colorbar(refl, label = 'dBZ', orientation = 'vertical', pad = .075)

#         # Get the current position of the colorbar's Axes
#         pos = hcolorbar.ax.get_position()

#         # Update the left position and keep the others the same
#         hcolorbar.ax.set_position([0.1, pos.y0, pos.width, pos.height])

#         # Move the horizontal colorbar to be centered below the plot
#         hcolorbar.ax.set_position([0.25, 0.08, 0.5, 0.02])  # [left, bottom, width, height]

#         # Move the vertical colorbar to be centered on the right side
#         vcolorbar.ax.set_position([0.92, 0.3, 0.02, 0.4])  # [left, bottom, width, height]

# #Save Figure
# fig.savefig(path+fig_name)

# #Clear Figure 
# plt.close()


/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:13: UserWarning: This figure was using constrained_layout==True, but that is incompatible with subplots_adjust and or tight_layout: setting constrained_layout==False. 
  del sys.path[0]
100%|██████████| 5/5 [00:31<00:00,  6.30s/it]


# The following code creates GIFs for each simualtion: Relfectivity at z  = 522 m, with black vertical velocity contours at z = 522 m, and vertical vorticity contours at z = 7.5 m (lowest grid level)

In [5]:
# Create A Function that Animates Each Storm
def full_animation(sim_path, num):
    # Figure Path and GIF Path
    path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
    gifname = f'/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/GIFs/Prelim_GIF_{num}.gif'
    
    for t in range(len(sim_names)): 
        # figure name
        fig_name = f'figure_%03d.png' % (t)
        
        # initialize plot 
        fig = plt.figure(figsize=(8,8))
        
        # Read in grid/time data 
        x_data = xr.open_dataset(sim_path + '/' + sim_names[t])['xh'] # scalar x-grid
        y_data = xr.open_dataset(sim_path + '/' + sim_names[t])['yh'] # scalar y-grid 
        time = np.int(xr.open_dataset(sim_path + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes
        
        # Read in vertical vorticity and reflectivity
        vorticity = xr.open_dataset(sim_path + '/' + sim_names[t])['zvort'].isel(time=0, zh=0) # vertical vorticity at z = 7.5m
        reflectivity = xr.open_dataset(sim_path + '/' + sim_names[t])['dbz'].isel(time = 0, zh = 17) # Relfectivity at z = 522 m
        velocity = xr.open_dataset(sim_path + '/' + sim_names[t])['winterp'].isel(time = 0, zh = 17) # vertical velocity at z= 522 m
        
        # plotting data 
        vort = plt.contourf(x_data, y_data, vorticity, cmap = 'bwr', alpha = 1, levels = np.arange(-.4, .41, .1),
                           vmin = -.4, vmax = .4)
        refl = plt.contourf(x_data, y_data, reflectivity, levels = np.arange(10,71, 5), vmin = 10, vmax = 70,
                           cmap = 'gist_ncar')
        w = plt.contour(x_data, y_data, velocity, levels = np.arange(5, 31, 5), colors ='k')
        
        # plot titles
        plt.title(f'Simulation {num} : Time = {t*5} min', fontsize =20)
        plt.xlabel = 'km'
        plt.ylabel = 'km'
        
        # Manually Set Axis Limits
        plt.xlim(-25, 15)
        plt.ylim(-15, 25)
        
        # Add global colorbar
        hcolorbar = fig.colorbar(vort, label = r'$\zeta_{7.5 \, m}$', orientation = 'horizontal', pad = 0.075, shrink=0.9)
        hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=14)
    
        vcolorbar = fig.colorbar(refl, label = 'dBZ', orientation = 'vertical')
    
        # Get the current position of the colorbar's Axes
        pos = hcolorbar.ax.get_position()

        # Update the left position and keep the others the same
        hcolorbar.ax.set_position([0.1, pos.y0, pos.width, pos.height])
    
        #Save Figure
        fig.savefig(path+fig_name)
    
        #Clear Figure 
        plt.close()
    
        
    #Combine Above Images into GIF
    #These variables control the time step (interval) and the length of the pause at the end of the animation (end_interval)
    interval = 0.3
    end_interval = 1.0

    #Iterating through all of the files in path, and then sorting the filenames
    imagefiles = os.listdir(path)
    # imagefiles.remove('.ipynb_checkpoints')


    image_filenames = []

    for image_filename in imagefiles[:t+1]:
        image_filenames.append(image_filename)
        image_filenames.sort()
    
    #Opening each image file and saving it to a list
    images = []
    for image_filename in tqdm(image_filenames[:t+1]):
        images.append(imageio.imread(path + image_filename))
      
    #Generating an array containing the duration to display each frame
    durations = np.ones(len(images))*interval
    durations[-1] = end_interval

    #Generating the animation itself
    imageio.mimsave(gifname, images, duration = durations.tolist())
        

In [7]:
# Animate All Simulations
#for sim in tqdm(range(len(sim_paths))):
    #full_animation(sim_paths[sim], sim+1)
# Animate A Single Simulation
x = 29
full_animation(sim_paths[x], x + 1)


/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:29: UserWarning: No contour levels were found within the data range.
100%|██████████| 25/25 [00:00<00:00, 122.91it/s]


# The following code creates a GIF of all the ensemble members together: Relfectivity at z = 522 m, with black vertical velocity contours at z = 522 m, and vertical vorticity contours at z = 7.5 m (lowest grid level)

In [19]:
# Tweak this perhaps to make the facecolor of each textbox represent NT, WT, or ST
# Create A Function that Animates the entire ensemble
def full_ensemble_dbz():
    # Figure Path and GIF Path
    path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
    gifname = f'/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/GIFs/full_ensemble_dbz.gif'
    
    
    # Iterate over each simulation time
    for t in tqdm(range(len(sim_names))):
        # Counter for each simulation
        count = 0
        
        # Figure Name
        fig_name = f'figure_%03d.png' % (t)
        
        # Initialize Figure
        fig, axs = plt.subplots(ncols = 6, nrows = 5, figsize = (30, 24), constrained_layout=True)
        fig.subplots_adjust(bottom=0.10, right=0.90)  # Make space below and on the right
        
        # Read in Each Simulation's Data
        x_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['xh'] # scalar x-grid
        y_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['yh'] # scalar y-grid 
        time = np.int(xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes

        # Iterate over Each Simulation to Populate the Columns/Rows or Each Panel
        for row in range(5):
            for col in range(6):
                
                # Read in vertical vorticity and reflectivity
                data =  xr.open_dataset(sim_paths[count] + '/' + sim_names[t])[['dbz', 'winterp','zvort']].isel(time=0, zh = [0,17])
                #vorticity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['zvort'].isel(time=0, zh=0) # vertical vorticity at z = 7.5m
                #reflectivity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['dbz'].isel(time = 0, zh = 17) # Relfectivity at z = 522 m
                #velocity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['winterp'].isel(time = 0, zh = 17) # vertical velocity at z= 522 m

                # plotting data 
                vort = axs[row, col].contourf(x_data, y_data, data['zvort'].isel(zh=0), cmap = 'bwr', alpha = 1, levels = np.arange(-.4, .41, .1),
                                   vmin = -.4, vmax = .4)
                refl = axs[row, col].contourf(x_data, y_data, data['dbz'].isel(zh=1), levels = np.arange(10,71, 5), vmin = 10, vmax = 70,
                                   cmap = 'gist_ncar')
                w = axs[row, col].contour(x_data, y_data, data['winterp'].isel(zh=1), levels = np.arange(5, 31, 5), colors ='k')

                # Manually Set Axis Limits
                axs[row, col].set_xlim(-25, 15)
                axs[row, col].set_ylim(-15, 25)
                
                # plot titles
                axs[row, col].text(12, 22.5, f'{count+1}', fontsize=12, 
                   bbox=dict(facecolor='palegoldenrod', boxstyle='round,pad=0.2'))
                #axs[row, col].xlabel = 'km'
                #axs[row, col].ylabel = 'km'
                
                # Update Counter
                count += 1
            
        # Titles for Entire Plot
        plt.suptitle(f'Full Ensemble: t = {5*t} min.', fontsize = 25, y = 0.91)

# --------------------------------------------------------------------------------------------------------------
        # Horizontal Colorbar (Bottom)
        cbar_ax_h = fig.add_axes([0.25, 0.05, 0.5, 0.02])  # [left, bottom, width, height]
        hcolorbar = fig.colorbar(vort, cax=cbar_ax_h, orientation='horizontal')
        hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=14)

        # Vertical Colorbar (Right)
        cbar_ax_v = fig.add_axes([0.91, 0.3, 0.02, 0.4])  # [left, bottom, width, height]
        vcolorbar = fig.colorbar(refl, cax=cbar_ax_v, orientation='vertical')
        vcolorbar.set_label('dBZ', fontsize=14)


#         # Add global colorbar
#         hcolorbar = fig.colorbar(vort, label = r'$\zeta_{7.5 \, m}$', orientation = 'horizontal', pad = 0.075, shrink=0.9)
#         hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=14)
#         vcolorbar = fig.colorbar(refl, label = 'dBZ', orientation = 'vertical', pad = .075)

#         # Get the current position of the colorbar's Axes
#         pos = hcolorbar.ax.get_position()

#         # Update the left position and keep the others the same
#         hcolorbar.ax.set_position([0.1, pos.y0, pos.width, pos.height])
        
#         # Move the horizontal colorbar to be centered below the plot
#         hcolorbar.ax.set_position([0.25, 0.08, 0.5, 0.02])  # [left, bottom, width, height]

#         # Move the vertical colorbar to be centered on the right side
#         vcolorbar.ax.set_position([0.92, 0.3, 0.02, 0.4])  # [left, bottom, width, height]

        #Save Figure
        fig.savefig(path+fig_name)

        #Clear Figure 
        plt.close()

# --------------------------------------------------------------------------------------------------------------
    #Combine Above Images into GIF
    #These variables control the time step (interval) and the length of the pause at the end of the animation (end_interval)
    interval = 0.3
    end_interval = 1.0

    #Iterating through all of the files in path, and then sorting the filenames
    imagefiles = os.listdir(path)
    # imagefiles.remove('.ipynb_checkpoints')


    image_filenames = []

    for image_filename in imagefiles[:t+1]:
        image_filenames.append(image_filename)
        image_filenames.sort()
    
    #Opening each image file and saving it to a list
    images = []
    for image_filename in tqdm(image_filenames[:t+1]):
        images.append(imageio.imread(path + image_filename))
      
    #Generating an array containing the duration to display each frame
    durations = np.ones(len(images))*interval
    durations[-1] = end_interval

    #Generating the animation itself
    imageio.mimsave(gifname, images, duration = durations.tolist())
        

In [20]:
full_ensemble_dbz()

# Change contour landing on zero for refl animations 

  0%|          | 0/25 [00:00<?, ?it/s]/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:19: UserWarning: This figure was using constrained_layout==True, but that is incompatible with subplots_adjust and or tight_layout: setting constrained_layout==False. 
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:41: UserWarning: No contour levels were found within the data range.
100%|██████████| 25/25 [00:02<00:00, 12.24it/s]


# The following creates a GIF of each simulation: 30 dBZ Reflectivity Contour at z = 993 m, Vorticity contours at z =7.5 m, and ground relative wind at z = 7.5 m

In [5]:
#Create A Function that Automates this process 

'Tweak this such that there is an additional argument (var name), so that I do not need a new cell everytime I want to change the variable'

def grw_full_animation(sim_path, num): 
    
    # Figure Path
    path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
    
    # GIF name
    gifname = f'/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/GIFs/grw_Full_Storm{num}.gif'
    
    # loop over to create individual images
    for t in range(len(sim_names)): 
        # Figure name 
        fig_name = f'figure_%03d.png' % (t)
        
        # Initialize Figure
        fig = plt.figure(figsize=(12,10))
        
        # Read In Grid/Time Data
        x_data = xr.open_dataset(sim_path + '/' + sim_names[t])['xh'] # scalar x-grid
        y_data = xr.open_dataset(sim_path + '/' + sim_names[t])['yh'] # scalar y-grid 
        time = np.int(xr.open_dataset(sim_path + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes
        
        # Read in Plotting Data
        u = xr.open_dataset(sim_path + '/' + sim_names[t])['uinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated u-winds 
        v = xr.open_dataset(sim_path + '/' + sim_names[t])['vinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated v-winds
        reflectivity = xr.open_dataset(sim_path + '/' + sim_names[t])['dbz'].isel(time=0, zh = 25) # interpolated reflectivity at 993 m
        vorticity = xr.open_dataset(sim_path + '/' + sim_names[t])['zvort'].isel(time=0, zh = 0) # z = 7.5 m interpolated vertical vorticity 
        
        # Ground Relative Wind Computation
        offset_u = 12.2 # u-component of storm motion
        offset_v = 12.5 # v-component of storm motion
        gr_wind = np.sqrt((u+offset_u)**2 + (v+offset_v)**2)
        
        # Plotting
        gr = plt.contourf(x_data, y_data, gr_wind, levels =  np.arange(0,71,10), vmin= 0, vmax = 70) # plotting gr_wind
        refl = plt.contour(x_data, y_data, reflectivity, levels=[30], colors='white') # 30-dbz reflectivity contour
        vort = plt.contour(x_data, y_data, vorticity, levels=np.arange(0.05,0.51, 0.05), cmap='Reds')
        
        # Colorbars 
        wind = plt.colorbar(gr, orientation='vertical', label = 'm/s')
        # Manually Create Legend For Vorticity
        legend_labels = [
            mlines.Line2D([], [], color='#FFCCCC', label='0.05'),
            mlines.Line2D([], [], color='#FF9999', label='0.1'),
            mlines.Line2D([], [], color='#FF8750', label='0.15'),
            mlines.Line2D([], [], color='#FF7500', label='0.2'),
            mlines.Line2D([], [], color='#FF6250', label='0.25'),
            mlines.Line2D([], [], color='#FF5000', label='0.3'),
            mlines.Line2D([], [], color='#FF3750', label='0.35'),
            mlines.Line2D([], [], color='#FF2500', label='0.4'),
            mlines.Line2D([], [], color='#FF1250', label='0.45'),
            mlines.Line2D([], [], color='#FF0000', label='0.5'),
        ]
        plt.legend(handles=legend_labels, title='Vorticity Levels ($s^{-1}$)', loc='lower left', fontsize='small')
        
        # Manually Set Axis Limits
        plt.xlim(-25, 15)
        plt.ylim(-15, 25)
        
        # Title Axes 
        plt.title(f'Storm {num}: Time = {t*5} min.', fontsize=20)
        plt.xlabel('km')
        plt.ylabel('km')
        
        # Save Fig and Close
        fig.savefig(path+fig_name)
        plt.close()
# --------------------------------------------------------------------------------------------------------------
        
    # TURN IMAGES INTO GIFs
        
    # Set Intervals
    interval = 0.35 # time step between frames
    end_interval = 1.0 # length of pause at the end of the animation
        
    # List all image files in directory
    imagefiles = os.listdir(path)
        
    # Create an empty list to append all images 
    image_filenames = []
        
    # Append images
    for image_filename in imagefiles[:t+1]:
        image_filenames.append(image_filename)
        image_filenames.sort()
            
    # open each image and save to a list 
    images = []
    for image_filename in tqdm(image_filenames[:t+1]):
        images.append(imageio.imread(path+image_filename))
        
    # Generating an array containing the duration of display for each frame
    durations = np.ones(len(images))*interval
    durations[-1] = end_interval
        
    # Create the GIF
    imageio.mimsave(gifname, images, duration = durations.tolist())
    

In [7]:
# Animate All Simulations
#for sim in tqdm(range(len(sim_paths))):
    #full_animation(sim_paths[sim], sim+1)
# Animate A Single Simulation
x = 29
grw_full_animation(sim_paths[x], x + 1)


/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:39: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:40: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:39: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:40: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:39: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:40: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:39: UserWarning: No contour levels were 

# Same as above but for the entire ensemble at once 

In [54]:
# Tweak this perhaps to make the facecolor of each textbox represent NT, WT, or ST
# Create A Function that Animates the entire ensemble
def full_ensemble_grw():
    # Figure Path and GIF Path
    path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
    gifname = f'/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/GIFs/full_ensemble_grw.gif'
    
    
    # Iterate over each simulation time
    for t in tqdm(range(len(sim_names))):
        # Counter for each simulation
        count = 0
        
        # Figure Name
        fig_name = f'figure_%03d.png' % (t)
        
        # Initialize Figure
        fig, axs = plt.subplots(ncols = 6, nrows = 5, figsize = (30, 24))
        
        # Read in Each Simulation's Data
        x_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['xh'] # scalar x-grid
        y_data = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['yh'] # scalar y-grid 
        time = np.int(xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes

        # Iterate over Each Simulation to Populate the Columns/Rows or Each Panel
        for row in range(5):
            for col in range(5):
                
                # Read in Plotting Data
                data =  xr.open_dataset(sim_paths[count] + '/' + sim_names[t])[['dbz', 'uinterp','vinterp','zvort']].isel(time=0, zh = [0,25])                
#               u = xr.open_dataset(sim_path + '/' + sim_names[t])['uinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated u-winds 
#               v = xr.open_dataset(sim_path + '/' + sim_names[t])['vinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated v-winds
#               reflectivity = xr.open_dataset(sim_path + '/' + sim_names[t])['dbz'].isel(time=0, zh = 25) # interpolated reflectivity at 993 m
#               vorticity = xr.open_dataset(sim_path + '/' + sim_names[t])['zvort'].isel(time=0, zh = 0) # z = 7.5 m interpolated vertical vorticity 

                # Ground Relative Wind Computation
                offset_u = 12.2 # u-component of storm motion
                offset_v = 12.5 # v-component of storm motion
                gr_wind = np.sqrt((data['uinterp'].isel(zh=0)+offset_u)**2 + (data['vinterp'].isel(zh=0)+offset_v)**2)

                # Plotting
                gr = axs[row, col].contourf(x_data, y_data, gr_wind, levels =  np.arange(0,71,10), vmin= 0, vmax = 70) # plotting gr_wind
                refl = axs[row, col].contour(x_data, y_data, data['dbz'].isel(zh=1), levels=[30], colors='white') # 30-dbz reflectivity contour
                vort = axs[row, col].contour(x_data, y_data, data['zvort'].isel(zh=0), levels=np.arange(0.05,0.51, 0.05), cmap='Reds')

                # Read in vertical vorticity and reflectivity
                #vorticity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['zvort'].isel(time=0, zh=0) # vertical vorticity at z = 7.5m
                #reflectivity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['dbz'].isel(time = 0, zh = 17) # Relfectivity at z = 522 m
                #velocity = xr.open_dataset(sim_paths[count] + '/' + sim_names[t])['winterp'].isel(time = 0, zh = 17) # vertical velocity at z= 522 m

                
                # Manually Set Axis Limits
                axs[row, col].set_xlim(-25, 15)
                axs[row, col].set_ylim(-15, 25)
                
                # plot titles
                axs[row, col].text(12, 22.5, f'{count+1}', fontsize = 12, bbox=dict(facecolor = 'palegoldenrod', boxstyle='round'))
                #axs[row, col].xlabel = 'km'
                #axs[row, col].ylabel = 'km'
                
                # Update Counter
                count += 1
            
        # Titles for Entire Plot
        plt.suptitle(f'Full Ensemble: t = {5*t} min.', fontsize = 20, y = 0.9)

# --------------------------------------------------------------------------------------------------------------

        # Add global colorbar
        #hcolorbar = fig.colorbar(vort, label = r'$\zeta_{7.5 \, m}$', orientation = 'horizontal', pad = 0.075, shrink=0.9)
        #hcolorbar.set_label(r'$\zeta_{7.5 \, m}$', fontsize=14)
        vcolorbar = fig.colorbar(gr, orientation='vertical', label = 'm/s')
        
        # Manually Create Legend For Vorticity
        legend_labels = [
            mlines.Line2D([], [], color='#FFCCCC', label='0.05'),
            mlines.Line2D([], [], color='#FF9999', label='0.1'),
            mlines.Line2D([], [], color='#FF8750', label='0.15'),
            mlines.Line2D([], [], color='#FF7500', label='0.2'),
            mlines.Line2D([], [], color='#FF6250', label='0.25'),
            mlines.Line2D([], [], color='#FF5000', label='0.3'),
            mlines.Line2D([], [], color='#FF3750', label='0.35'),
            mlines.Line2D([], [], color='#FF2500', label='0.4'),
            mlines.Line2D([], [], color='#FF1250', label='0.45'),
            mlines.Line2D([], [], color='#FF0000', label='0.5'),
        ]
        plt.legend(handles=legend_labels, title='Vorticity Levels ($s^{-1}$)', bbox_to_anchor=[1.4, 1.2, 0.5, 0.02], fontsize='medium')
        

        # Get the current position of the colorbar's Axes
        #pos = hcolorbar.ax.get_position()

        # Update the left position and keep the others the same
        #hcolorbar.ax.set_position([0.1, pos.y0, pos.width, pos.height])
        
        # Move the horizontal colorbar to be centered below the plot
        #hcolorbar.ax.set_position([0.25, 0.08, 0.5, 0.02])  # [left, bottom, width, height]

        # Move the vertical colorbar to be centered on the right side
        vcolorbar.ax.set_position([0.91, 0.3, 0.02, 0.4])  # [left, bottom, width, height]

        #Save Figure
        fig.savefig(path+fig_name)

        #Clear Figure 
        plt.close()

# --------------------------------------------------------------------------------------------------------------
    #Combine Above Images into GIF
    #These variables control the time step (interval) and the length of the pause at the end of the animation (end_interval)
    interval = 0.3
    end_interval = 1.0

    #Iterating through all of the files in path, and then sorting the filenames
    imagefiles = os.listdir(path)
    # imagefiles.remove('.ipynb_checkpoints')


    image_filenames = []

    for image_filename in imagefiles[:t+1]:
        image_filenames.append(image_filename)
        image_filenames.sort()
    
    #Opening each image file and saving it to a list
    images = []
    for image_filename in tqdm(image_filenames[:t+1]):
        images.append(imageio.imread(path + image_filename))
      
    #Generating an array containing the duration to display each frame
    durations = np.ones(len(images))*interval
    durations[-1] = end_interval

    #Generating the animation itself
    imageio.mimsave(gifname, images, duration = durations.tolist())
        

In [ ]:
full_ensemble_grw()

  0%|          | 0/25 [00:00<?, ?it/s]/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43

/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were 

/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were 

/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were 

/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:43: UserWarning: No contour levels were 

/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: No contour levels were 

# The following creates a GIF of each simulation: 30 dBZ Reflectivity Contour at z = 993 m, Vorticity contours at z =7.5 m, and non-derivable variable of choice at z = 7.5 m

In [47]:
#Create A Function that Automates this process 

def var_full_animation(sim_path, num, var_name): 
    
    # Figure Path
    path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
    
    # GIF name
    gifname = f'/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/GIFs/{var_name}_Full_Storm{num}.gif'
    
    # loop over to create individual images
    for t in range(len(sim_names)): 
        # Figure name 
        fig_name = f'figure_%03d.png' % (t)
        
        # Initialize Figure
        fig = plt.figure(figsize=(12,10))
        
        # Read In Grid/Time Data
        x_data = xr.open_dataset(sim_path + '/' + sim_names[t])['xh'] # scalar x-grid
        y_data = xr.open_dataset(sim_path + '/' + sim_names[t])['yh'] # scalar y-grid 
        time = np.int(xr.open_dataset(sim_path + '/' + sim_names[t])['time'][0].values/10**9)/60 # time in minutes
        
        # Read in Plotting Data
        variable = xr.open_dataset(sim_path + '/' + sim_names[t])[var_name].isel(time=0, zh = 0) # z = 7.5 m interpolated variable
        #u = xr.open_dataset(sim_path + '/' + sim_names[t])['uinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated u-winds 
        #v = xr.open_dataset(sim_path + '/' + sim_names[t])['vinterp'].isel(time=0, zh = 0) # z = 7.5 m interpolated v-winds
        reflectivity = xr.open_dataset(sim_path + '/' + sim_names[t])['dbz'].isel(time=0, zh = 25) # interpolated reflectivity at 993 m
        vorticity = xr.open_dataset(sim_path + '/' + sim_names[t])['zvort'].isel(time=0, zh = 0) # z = 7.5 m interpolated vertical vorticity 
        
        # Ground Relative Wind Computation
        #offset_u = 12.2 # u-component of storm motion
        #offset_v = 12.5 # v-component of storm motion
        #gr_wind = np.sqrt((u+offset_u)**2 + (v+offset_v)**2)
        
        # Plotting
        bottom = var.min()
        top = var.max()
        var = plt.contourf(x_data, y_data, variable, levels =  np.linspace(bottom,top,100), vmin= bottom, vmax = top) # plotting qv
        refl = plt.contour(x_data, y_data, reflectivity, levels=[30], colors='white') # 30-dbz reflectivity contour
        vort = plt.contour(x_data, y_data, vorticity, levels=np.arange(0.05,0.51, 0.05), cmap='Reds')
        
        # Colorbars 
        moisture = plt.colorbar(vapor, orientation='vertical', label = 'g/kg')
        # Manually Create Legend For Vorticity
        legend_labels = [
            mlines.Line2D([], [], color='#FFCCCC', label='0.05'),
            mlines.Line2D([], [], color='#FF9999', label='0.1'),
            mlines.Line2D([], [], color='#FF8750', label='0.15'),
            mlines.Line2D([], [], color='#FF7500', label='0.2'),
            mlines.Line2D([], [], color='#FF6250', label='0.25'),
            mlines.Line2D([], [], color='#FF5000', label='0.3'),
            mlines.Line2D([], [], color='#FF3750', label='0.35'),
            mlines.Line2D([], [], color='#FF2500', label='0.4'),
            mlines.Line2D([], [], color='#FF1250', label='0.45'),
            mlines.Line2D([], [], color='#FF0000', label='0.5'),
        ]
        plt.legend(handles=legend_labels, title='Vorticity Levels ($s^{-1}$)', loc='lower left', fontsize='small')
        
        # Manually Set Axis Limits
        plt.xlim(-35, 15)
        plt.ylim(-15, 35)
        
        # Title Axes 
        plt.title(f'Storm {num}: Time = {t*5} min.', fontsize=20)
        plt.xlabel('km')
        plt.ylabel('km')
        
        # Save Fig and Close
        fig.savefig(path+fig_name)
        plt.close()
        
    # TURN IMAGES INTO GIFs
        
    # Set Intervals
    interval = 0.35 # time step between frames
    end_interval = 1.0 # length of pause at the end of the animation
        
    # List all image files in directory
    imagefiles = os.listdir(path)
        
    # Create an empty list to append all images 
    image_filenames = []
        
    # Append images
    for image_filename in imagefiles[:t+1]:
        image_filenames.append(image_filename)
        image_filenames.sort()
            
    # open each image and save to a list 
    images = []
    for image_filename in tqdm(image_filenames[:t+1]):
        images.append(imageio.imread(path+image_filename))
        
    # Generating an array containing the duration of display for each frame
    durations = np.ones(len(images))*interval
    durations[-1] = end_interval
        
    # Create the GIF
    imageio.mimsave(gifname, images, duration = durations.tolist())
    

In [30]:
# Animate All Simulations
for sim in tqdm(range(len(sim_paths))):
    full_animation(sim_paths[sim], sim+1)
# Animate A Single Simulation
# x = 24
# full_animation(sim_paths[x], x + 1)


  0%|          | 0/26 [00:00<?, ?it/s]/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:38: UserWarning: No contour levels were found within the data range.
/storage/home/bsh5393/new/lib64/python3.6/site-packages/ipykernel_launcher.py:39: UserWarning: No contour levels were found within the data range.

100%|██████████| 26/26 [18:29<00:00, 42.68s/it]


# The following code creates a GIF of the original Storm16 at 5 min intervals in order to loop at the same pace as the current simulations

In [77]:
#Create A GIF of Storm 16 at 5 min intervals 

path = '/storage/work/bsh5393/Masters Thesis/Pre-Storm Environment Soundings/Figure Builder/'
gifname = '/storage/work/bsh5393/Variability Study/Data/InterpolationData/GIFs/storm16.gif'

for t in range(len(Sim1_dbz)):
    #Choose Random Sounding ID 
    image_filename = "figure_%03d.png" % (t)
    
    #figure initialization
    fig = plt.figure(figsize = (10,8))
    plt.contourf(x_data,y_data, Storm16_dbz[t].isel(nk = 17), levels=100, cmap='gist_ncar')
    plt.colorbar()
    plt.title(f'time = {65+5*t} min')
    plt.ylim(0)
    #Save Figure
    fig.savefig(path+image_filename)
    
    #Clear Figure 
    plt.close()
    
    
    #Combine Above Images into GIF
#These variables control the time step (interval) and the length of the pause at the end of the animation (end_interval)
interval = 0.2
end_interval = 1.0

#Iterating through all of the files in path, and then sorting the filenames
imagefiles = os.listdir(path)
imagefiles.remove('.ipynb_checkpoints')


image_filenames = []

for image_filename in imagefiles[:t]:
    image_filenames.append(image_filename)
image_filenames.sort()
    
#Opening each image file and saving it to a list
images = []
for image_filename in image_filenames[:t]:
    images.append(imageio.imread(path + image_filename))
      
#Generating an array containing the duration to display each frame
durations = np.ones(len(images))*interval
durations[-1] = end_interval

#Generating the animation itself
imageio.mimsave(gifname, images, duration = durations.tolist())